In [100]:
import json

Data = json.load(open("resultconf0.75.json","r"))
predictedData = {}
for key, elem in Data.items():
    print(key, elem)
    predictedData[key] = json.loads(elem)

f = json.load(open("cocodoomData/run-test.json","r"))
groundTruthData = {}
for images in f["images"]:
    groundTruthData[images["id"]] = {"file_name":images["file_name"], "bbox":[], "category_id":[]}

for annotation in f["annotations"]:
    box = annotation["bbox"]
    box[2] += box[0]
    box[3] += box[1]
    groundTruthData[annotation["image_id"]]["bbox"].append(box)
    groundTruthData[annotation["image_id"]]["category_id"].append(annotation["category_id"])

iou = {}

C:\Users\engel\Documents\cocoDoom\data\images\run3\000002.png []
C:\Users\engel\Documents\cocoDoom\data\images\run3\000022.png []
C:\Users\engel\Documents\cocoDoom\data\images\run3\000042.png []
C:\Users\engel\Documents\cocoDoom\data\images\run3\000062.png []
C:\Users\engel\Documents\cocoDoom\data\images\run3\000082.png [
  {
    "name": "a",
    "class": 0,
    "confidence": 0.79265296459198,
    "box": {
      "x1": 50.102996826171875,
      "y1": 116.70329284667969,
      "x2": 72.96937561035156,
      "y2": 152.53114318847656
    }
  }
]
C:\Users\engel\Documents\cocoDoom\data\images\run3\000102.png [
  {
    "name": "a",
    "class": 0,
    "confidence": 0.9789676070213318,
    "box": {
      "x1": 45.34595489501953,
      "y1": 61.01594543457031,
      "x2": 227.61871337890625,
      "y2": 200.0
    }
  },
  {
    "name": "G",
    "class": 30,
    "confidence": 0.9689554572105408,
    "box": {
      "x1": 14.24981689453125,
      "y1": 76.91859436035156,
      "x2": 91.37118530273

In [101]:
print("Predicted Data: ", predictedData[list(predictedData.keys())[0]])
print("Ground Truth Data: ", groundTruthData[list(groundTruthData.keys())[0]])

print(type(predictedData))

Predicted Data:  []
Ground Truth Data:  {'file_name': 'run3/map01/rgb/000002.png', 'bbox': [[98, 112, 116, 137], [138, 104, 152, 124]], 'category_id': [1, 1]}
<class 'dict'>


In [102]:
def computeIoU(predictedBox, trueBox):
    x1 = max(predictedBox[0], trueBox[0])
    y1 = max(predictedBox[1], trueBox[1])
    x2 = min(predictedBox[2], trueBox[2])
    y2 = min(predictedBox[3], trueBox[3])
    intersection = max(0, x2-x1) * max(0, y2-y1)
    union =( predictedBox[2]-predictedBox[0])*(predictedBox[3]-predictedBox[1]) + (trueBox[2]-trueBox[0])*(trueBox[3]-trueBox[1]) - intersection
    # print("Intersection: ", intersection)
    # print("Union: ", union)
    return intersection/union


In [103]:
print(len(predictedData.keys()))
print(len(groundTruthData.keys()))

iouMoyenne = 0
falsePrediction = 0
totErrorNbBox = 0
total = 0
for predicetedkey, predictedvalue,truevalue in zip(predictedData.keys(), predictedData.values(),groundTruthData.values()):
    iou[predicetedkey] = {'metric':[]}
    ErrorNbBox = 0
    if (len(predictedvalue) != len(truevalue["bbox"])):
        if (len(predictedvalue) > len(truevalue["bbox"])):
            ErrorNbBox = len(predictedvalue) - len(truevalue["bbox"])
        else:
            ErrorNbBox = len(truevalue["bbox"]) - len(predictedvalue)
        totErrorNbBox += abs(ErrorNbBox)
    for trueBox,trueid in zip(truevalue["bbox"], truevalue["category_id"]):
        computedIoU = 0
        predictedIdMaxIoU = 0
        for predicted in predictedvalue:
            predictedBox = [predicted['box']["x1"], predicted['box']["y1"], predicted['box']["x2"], predicted['box']["y2"]]
            predictedId = predicted["class"]+1
            newIoU = computeIoU(predictedBox, trueBox)
            if (computedIoU<newIoU):
                computedIoU = newIoU
                predictedIdMaxIoU = predictedId
        if (len(predictedvalue) != 0):
            falsePrediction += 1 if predictedIdMaxIoU!=trueid else 0
            if predictedIdMaxIoU!=trueid:
                print("Predicted ID: ", predictedId)
                print("True ID: ", trueid)
        total += 1
        iouMoyenne += computedIoU
        iou[predicetedkey]['metric'].append({ "iou": computedIoU, "predictedId": predictedId})
        iou[predicetedkey]['errorNbBox'] = ErrorNbBox
            



print("IoU Moyenne: ", iouMoyenne/total)
print("False Prediction: ", falsePrediction)
print("Total: ", total)
print("Total Error Nb Box: ", totErrorNbBox)
iou['globalMetrics'] = {"IoUMoyenne": iouMoyenne/total, "FalsePrediction": falsePrediction, "Total": total, "TotalErrorNbBox": totErrorNbBox}
json.dump(iou, open("iouconf0.75.json","w"))


5907
5907
Predicted ID:  1
True ID:  1
Predicted ID:  1
True ID:  53
Predicted ID:  31
True ID:  38
Predicted ID:  1
True ID:  38
Predicted ID:  1
True ID:  45
Predicted ID:  36
True ID:  45
Predicted ID:  36
True ID:  45
Predicted ID:  31
True ID:  1
Predicted ID:  31
True ID:  1
Predicted ID:  31
True ID:  38
Predicted ID:  31
True ID:  38
Predicted ID:  39
True ID:  53
Predicted ID:  39
True ID:  38
Predicted ID:  39
True ID:  38
Predicted ID:  1
True ID:  63
Predicted ID:  39
True ID:  53
Predicted ID:  31
True ID:  38
Predicted ID:  31
True ID:  38
Predicted ID:  31
True ID:  31
Predicted ID:  31
True ID:  38
Predicted ID:  31
True ID:  38
Predicted ID:  31
True ID:  38
Predicted ID:  31
True ID:  38
Predicted ID:  31
True ID:  38
Predicted ID:  31
True ID:  38
Predicted ID:  11
True ID:  31
Predicted ID:  11
True ID:  1
Predicted ID:  11
True ID:  11
Predicted ID:  36
True ID:  45
Predicted ID:  36
True ID:  45
Predicted ID:  36
True ID:  45
Predicted ID:  36
True ID:  45
Predict